### Create the process for merging new or corrected site data

In [32]:
import geopandas as gpd
import pandas as pd
import numpy as np
import os
import folium
# use these if you are using the pandas dataframe view, I prefer itables because it is interactive
# pd.set_option('display.max_columns', None)
# pd.set_option('display.max_rows', None)

# this makes dataframes viewable as interactive tables with search and sort
from itables import init_notebook_mode
init_notebook_mode(all_interactive=True)

import itables.options as opt
opt.maxBytes = 0 ### this removes size limits for interactive table


<IPython.core.display.Javascript object>

#### ** helpful links and snippets

In [33]:
# os.getcwd() # check what the working directory is

# keyboard shortcuts
# https://noteable.io/blog/jupyter-notebook-shortcuts-boost-productivity/

### set working directory to the github repo directory
this is where you change this so that it works on your computer too

In [34]:
os.chdir('/Users/sarahodges/spatial/SAVI/hudson_access/data/published')

### Import existing site points data

 - this is actually the **hap_site_points_fieldupdates_surveyintegration_8-2-23.geojson** data from sara eichner, with the new entries removed from the dataset
 - using this to create the process of site data updates

In [35]:
current_site_points = gpd.read_file('data/hap_site_points.geojson')
# len(current_site_points.columns)
current_site_points

site_id         act_codes                             access_id  \
0            174  FISH, HPBL, MPBL                      4, 516, 151, 787   
1             29  MPBL, HPBL, FISH                   126, 83, 1613, 1803   
2            183              FISH                      1, 443, 511, 800   
3             54  MPBL, HPBL, FISH     291, 433, 293, 166, 117, 000, 000   
4              1              HPBL  9, 097, 941, 594, 168, 710, 000, 000   
..           ...               ...                                   ...   
747  remove dupe              MPBL                                   509   
748          215              HPBL                     16, 752, 031, 621   
749        71975              HPBL                             1621_HPBL   
750          157  MPBL, HPBL, FISH                           3, 121, 599   
751          161              FISH                      1, 517, 201, 721   

                                site_name                   site_label  \
0                          Bayswater Park                         None   
1                   Conference House Park                         None   
2                 Mt Loretto Natural Area                         None   
3                        Lemon Creek Park                         None   
4                          Riverside Park                         None   
..                                    ...                          ...   
747                      River Barge Park                         None   
748             Gowanus Canal Sponge Park                         None   
749  Lowe's Gowanus Parklet & Boat Launch                         None   
750               Louis Valentino Jr Park                         None   
751                       Shore Road Park  Shore Road Park and Parkway   

                                          site_address  \
0    Dwight Ave, Seagirt Blvd between Beach 38th St...   
1    Hylan Blvd & Satterlee St, Staten Island, Hyla...   
2    End of Sharrotts Ave at Hylan Blvd, Hylan Blvd...   
3                                                 None   
4                             W 79th St End, Manhattan   
..                                                 ...   
747                                               None   
748               166 2nd St, Brooklyn, Foot of 2nd St   
749                   539 Smith St, Brooklyn, NY 11231   
750               End of Coffey St, Red Hook, Brooklyn   
751     Bay Ridge Ave (69th St) at Shore Rd, Bay Ridge   

                                      site_description  \
0    This waterfront park is named, in part, for Ju...   
1    The site of a legendary display of American de...   
2                                                 None   
3                             Yellow trail nature path   
4    This site is considered a cultural resource. R...   
..                                                 ...   
747                                               None   
748                                               None   
749                                               None   
750  Now surrounded by industrial, residential, and...   
751  An expansive park along the Shore Parkway Gree...   

                                    hours_info open_close_date   fee  ...  \
0    Sunrise to Sunset (April 1 to December 1)            None  None  ...   
1    Sunrise to Sunset (April 1 to December 1)            None     Y  ...   
2                                         None            None  None  ...   
3                                         None            None  None  ...   
4    Sunrise to Sunset (April 1 to December 1)            None  None  ...   
..                                         ...             ...   ...  ...   
747                                       None            None  None  ...   
748                                       None            None  None  ...   
749                                       None            None  None  ...   
750  Sunrise to Sunset (April 1 to December

In [36]:
#### create a site_score dataframe and remove from data
site_score = current_site_points.copy()[['site_id', 'site_score']]
#site_score.head()
# site_points.columns.to_list()

['site_id',
 'act_codes',
 'access_id',
 'site_name',
 'site_label',
 'site_address',
 'site_description',
 'hours_info',
 'open_close_date',
 'fee',
 'fee_amount',
 'public_transit',
 'public_transit_description',
 'url_public',
 'phone_public',
 'email_public',
 'site_manager',
 'phone_site_manager',
 'email_site_manager',
 'access_type',
 'access_type_other',
 'accessibility_description',
 'safety',
 'use_limits',
 'water_depth_est',
 'program_YN',
 'program_name',
 'program_description',
 'program_hours',
 'program_id',
 'program_phone',
 'program_url',
 'program_contact',
 'amenities_description',
 'restrooms',
 'changing_station',
 'food',
 'drinking_water',
 'walking_trails',
 'equipment_rental',
 'boat_access',
 'boat_launch_YN',
 'bike_path_accessible',
 'bike_path_access_description',
 'bike_parking_rack',
 'picnic_area',
 'playground',
 'parking',
 'parking_description',
 'pets_allowed',
 'wheelchair_access_amenities',
 'wheelchair_access_restrooms',
 'wheelchair_access_trai

### Make corrections to existing site points data

In [37]:
# Filtering and Mutating operations
site_points = (
    current_site_points
    .query("site_id != 'remove dupe'")
    .drop(columns='site_score')  # Remove the 'site_score' column
    .assign(
        site_name=current_site_points["site_name"].where(current_site_points["site_name"] != "Fair Haven Rd & Fairwaters Lane", "Fair Haven Pier"),
        site_id=current_site_points["site_id"].where(current_site_points["site_name"] != "Fair Haven Rd & Fairwaters Lane", 540232),
        site_description=current_site_points['site_description'].str.replace('This site is considered an historic landmark', '')
    )
)

# site_points['site_id'] = pd.to_numeric(site_points['site_id'], errors='coerce')  
### the highest site_id (other than one that ends in 999 for a specific reason, is 900136)

site_points_df = pd.DataFrame(site_points.drop(columns='geometry'))
site_points_df

site_id         act_codes                             access_id  \
0       174  FISH, HPBL, MPBL                      4, 516, 151, 787   
1        29  MPBL, HPBL, FISH                   126, 83, 1613, 1803   
2       183              FISH                      1, 443, 511, 800   
3        54  MPBL, HPBL, FISH     291, 433, 293, 166, 117, 000, 000   
4         1              HPBL  9, 097, 941, 594, 168, 710, 000, 000   
..      ...               ...                                   ...   
746      98  MPBL, FISH, HPBL                      6, 416, 501, 784   
748     215              HPBL                     16, 752, 031, 621   
749   71975              HPBL                             1621_HPBL   
750     157  MPBL, HPBL, FISH                           3, 121, 599   
751     161              FISH                      1, 517, 201, 721   

                                site_name                   site_label  \
0                          Bayswater Park                         None   
1                   Conference House Park                         None   
2                 Mt Loretto Natural Area                         None   
3                        Lemon Creek Park                         None   
4                          Riverside Park                         None   
..                                    ...                          ...   
746       Breezy Point Tip at Jamaica Bay                         None   
748             Gowanus Canal Sponge Park                         None   
749  Lowe's Gowanus Parklet & Boat Launch                         None   
750               Louis Valentino Jr Park                         None   
751                       Shore Road Park  Shore Road Park and Parkway   

                                          site_address  \
0    Dwight Ave, Seagirt Blvd between Beach 38th St...   
1    Hylan Blvd & Satterlee St, Staten Island, Hyla...   
2    End of Sharrotts Ave at Hylan Blvd, Hylan Blvd...   
3                                                 None   
4                             W 79th St End, Manhattan   
..                                                 ...   
746  End of Rockaway Point Blvd, Beach 222nd Street...   
748               166 2nd St, Brooklyn, Foot of 2nd St   
749                   539 Smith St, Brooklyn, NY 11231   
750               End of Coffey St, Red Hook, Brooklyn   
751     Bay Ridge Ave (69th St) at Shore Rd, Bay Ridge   

                                      site_description  \
0    This waterfront park is named, in part, for Ju...   
1    The site of a legendary display of American de...   
2                                                 None   
3                             Yellow trail nature path   
4    This site is considered a cultural resource. R...   
..                                                 ...   
746  It’s easy to forget one is in New York City at...   
748                                               None   
749                                               None   
750  Now surrounded by industrial, residential, and...   
751  An expansive park along the Shore Parkway Gree...   

                                    hours_info open_close_date   fee  ...  \
0    Sunrise to Sunset (April 1 to December 1)            None  None  ...   
1    Sunrise to Sunset (April 1 to December 1)            None     Y  ...   
2                                         None            None  None  ...   
3                                         None            None  None  ...   
4    Sunrise to Sunset (April 1 to December 1)            None  None  ...   
..                                         ...             ...   ...  ...   
746                                       None            None  None  ...   
748                                       None            None  None  ...   
749                                       None            None  None  ...   
750  Sunrise to Sunset (April 1 to December 1)            None  None  ...   
751                  

## IMPORT survey data from summer site visits and process
Alyssa collected these over the summer - up to July 28 using the Survey123 s

In [38]:
## add new survey data
raw_surv_new = pd.read_csv('data/data_updates/Hudson_Access_Project_Data_Survey_0.csv')

In [39]:
### check the column differences

site_cols = site_points_df.columns
survey_cols = raw_surv_new.columns

site_cols.difference(survey_cols)

Index([], dtype='object')

#### Function to create new act_codes based on Alyssa's YN columns

 - if none are defined as Y, then act_codes == VISUAL
 - discuss with Sara E, we decided to define them all as FISH, but when I looked at them it didn;t seem right

In [40]:
def create_new_act_codes(row):
    activities = []
    if row['FISH_YN'] == 'Y':
        activities.append('FISH')
    if row['SWIM_YN'] == 'Y':
        activities.append('SWIM')
    if row['HPBL_YN'] == 'Y':
        activities.append('HPBL')
    if row['MPBL_YN'] == 'Y':
        activities.append('MPBL')
        
    if not activities:
        activities.append('VISUAL')
    
    return ','.join(activities)

#### Handle new sites

 - create dataframe of sites that aren't in the existing dataset
 - add source info
 - add site_id
 - check and update act_codes

In [41]:
# add site_id to all the new sites

new_sites = (
    raw_surv_new
    .query("site_id == 'needs id'")
    .assign(
        source = "Alyssa, summer 23 new site"
    )
    .reset_index(drop=True)
)

new_sites['site_id'] = new_sites.index + 900137 ### the highest site_id (other than one that ends in 999 for a specific reason, is 900136)

In [42]:
new_sites['act_codes'] = new_sites.apply(create_new_act_codes, axis=1)

new_sites

ObjectID                              GlobalID county  lat  lon  \
0         45  45838631-7518-41eb-88ed-83f029354329    NaN  NaN  NaN   
1         58  ce0c11d9-c208-47be-8ea0-6c85319c077a    NaN  NaN  NaN   
2         57  6101c1a0-d8f7-4854-8034-9bb337ec231e    NaN  NaN  NaN   
3         46  df04d5fe-95b2-44ad-8d6c-1a3dd770f31f    NaN  NaN  NaN   
4         41  6095d94b-8a52-4368-8a99-1f2088a690f0    NaN  NaN  NaN   
5         56  7fd1fede-5f52-4c57-85bb-206accf6490c    NaN  NaN  NaN   
6         36  26b60cc7-0f57-49f6-8efa-e16ec0ddf0a2    NaN  NaN  NaN   
7         47  5e0fd162-5841-4784-8510-7786ef285ce4    NaN  NaN  NaN   
8         35  2ef63fac-3550-43fd-8041-d1f77a2b375e    NaN  NaN  NaN   
9         38  b9a61410-d38b-4e79-88ee-cfc5f723fb58    NaN  NaN  NaN   
10        44  4fe69fc5-ce1e-4e3d-86f2-c08ee115b7d3    NaN  NaN  NaN   
11        59  34e95d22-a291-4777-86bf-2081c92aa57a    NaN  NaN  NaN   
12        53  50241fa8-f460-42e5-8cf4-3551107853d1    NaN  NaN  NaN   

   municipality natural_no  site_id access_id                      source  \
0           NaN        NaN   900137       NaN  Alyssa, summer 23 new site   
1           NaN        NaN   900138       NaN  Alyssa, summer 23 new site   
2           NaN        NaN   900139       NaN  Alyssa, summer 23 new site   
3           NaN        NaN   900140       NaN  Alyssa, summer 23 new site   
4           NaN        NaN   900141       NaN  Alyssa, summer 23 new site   
5           NaN        NaN   900142       NaN  Alyssa, summer 23 new site   
6           NaN        NaN   900143       NaN  Alyssa, summer 23 new site   
7           NaN        NaN   900144       NaN  Alyssa, summer 23 new site   
8           NaN        NaN   900145       NaN  Alyssa, summer 23 new site   
9           NaN        NaN   900146       NaN  Alyssa, summer 23 new site   
10          NaN        NaN   900147       NaN  Alyssa, summer 23 new site   
11          NaN        NaN   900148       NaN  Alyssa, summer 23 new site   
12          NaN        NaN   900149       NaN  Alyssa, summer 23 new site   

    ... access_type access_type_other water_depth_est  \
0   ...        pier               NaN             NaN   
1   ...        pier               NaN             NaN   
2   ...       rocky               NaN             NaN   
3   ...       rocky               NaN             NaN   
4   ...       beach               NaN             NaN   
5   ...        dock               NaN             NaN   
6   ...       rocky               NaN             NaN   
7   ...        pier               NaN             NaN   
8   ...         NaN               NaN             NaN   
9   ...         NaN               NaN             NaN   
10  ...         NaN               NaN             NaN   
11  ...  pier,rocky               NaN             NaN   
12  ...       other     Floating Lab              NaN   

                             water_quality_monitoring  \
0                                                 NaN   
1                                                 NaN   
2                                                 NaN   
3   https://www.riverkeeper.org/water-quality/huds...   
4   https://www.riverkeeper.org/water-quality/citi...   
5                                                 NaN   
6   https://www.riverkeeper.org/water-quality/citi...   
7   https://www.riverkeeper.org/water-quality/huds...   
8   https://www.riverkeeper.org/water-quality/huds...   
9   https://www.weatherlink.com/embeddablePage/sho...   
10                                                NaN   
11  https://www.riverkeeper.org/water-quality/huds...   
12  https://www.riverkeeper.org/water-quality/huds...   

                                     open_close_date walking_trails  \
0                                                NaN            NaN   
1                                                NaN              Y   
2                                                NaN              Y   
3                                               

#### Handle updated sites

 - create dataframe of sites that are in the existing dataset
 - add spource info
 - create dataframe of information in old hap_site_points to check if there are any issues
 - check and update act_codes

In [43]:
## create a dataframe of updated site_ids 

updated_sites = (
    raw_surv_new
    .query("site_id != 'needs id'")
    .assign(
        source = "Alyssa, summer 23 updated site",
        act_codes = raw_surv_new.apply(create_new_act_codes, axis=1)
    )
    # .filter(['site_id', 'site_name'], axis="columns") # first look at the names to check
)

#updated_sites

# this is the old sites, can use this to compare later
replaced_sites = site_points_df.merge(updated_sites[['site_id']], on='site_id', how='inner')

# explored in the console
# len(updated_sites) = 18
# len(replaced_sites) = 19
### there is a dupe in the original data, I will make sure it is removed when I bind all the dfs togther

## Create updated hap_site_points

 - use antijoin to remove the sites that have been updated
 - concat to combine old, updated, and new

In [44]:
# antijoin
sites_no_update = site_points_df.merge(updated_sites[['site_id']], how='left', indicator=True).query('_merge == "left_only"').drop('_merge', axis="columns")

### test to determine if the antijoin worked as predicted, should == 0
len(site_points_df) - len(replaced_sites) - len(sites_no_update)

0

In [45]:
new_hap_site_points_temp = pd.concat([sites_no_update, updated_sites], ignore_index=True)

#### checks

len(new_hap_site_points_temp)
# 750, good, it removed the dupe in the og data

750

In [46]:
new_hap_site_points = pd.concat([new_hap_site_points_temp, new_sites], ignore_index=True)
len(new_hap_site_points)
# 763 = correct

763

### Checks to ensure that the new data will work with the website

 - act_codes have no spaces
 - all sites have act_codes
 - all sites have site_id

In [47]:
### remove spaces in the act_codes

new_hap_site_points['act_codes'] = new_hap_site_points['act_codes'].str.replace(r'\s*,\s*', ',')


In [48]:
### check for spaces or NAs - will need to figure out what to do about VISUAL and STE

new_hap_site_points['act_codes'].unique()

array(['FISH,HPBL,MPBL', 'MPBL,HPBL,FISH', 'FISH', 'HPBL',
       'FISH,MPBL,HPBL', 'HPBL,MPBL', 'MPBL', 'SWIM', 'HPBL,FISH',
       'MPBL,FISH', 'MPBL,HPBL', 'FISH,SWIM', 'FISH,HPBL', 'HPBL,STE',
       'MPBL,FISH,SWIM,HPBL', 'HPBL,MPBL,FISH', 'MPBL,HPBL,FISH,SWIM',
       'FISH,MPBL', 'SWIM,FISH', 'HPBL,SWIM,MPBL', 'MPBL,SWIM',
       'HPBL,FISH,MPBL', 'MPBL,HPBL,SWIM,FISH', 'MPBL,SWIM,HPBL,FISH',
       'SWIM,MPBL,HPBL,FISH', 'HPBL,SWIM,FISH', 'SWIM,FISH,HPBL',
       'HPBL,SWIM', 'MPBL,FISH,HPBL', 'FISH,SWIM,MPBL,HPBL',
       'FISH,MPBL,HPBL,SWIM', 'MPBL,FISH,SWIM', 'VISUAL'], dtype=object)

In [49]:
### count the NA site_ids

new_hap_site_points['site_id'].isna().sum() 

0

In [50]:
new_hap_site_points

site_id       act_codes                             access_id  \
0       174  FISH,HPBL,MPBL                      4, 516, 151, 787   
1        29  MPBL,HPBL,FISH                   126, 83, 1613, 1803   
2       183            FISH                      1, 443, 511, 800   
3        54  MPBL,HPBL,FISH     291, 433, 293, 166, 117, 000, 000   
4         1            HPBL  9, 097, 941, 594, 168, 710, 000, 000   
..      ...             ...                                   ...   
758  900145          VISUAL                                   NaN   
759  900146          VISUAL                                   NaN   
760  900147          VISUAL                                   NaN   
761  900148            FISH                                   NaN   
762  900149          VISUAL                                   NaN   

                                       site_name site_label  \
0                                 Bayswater Park       None   
1                          Conference House Park       None   
2                        Mt Loretto Natural Area       None   
3                               Lemon Creek Park       None   
4                                 Riverside Park       None   
..                                           ...        ...   
758                            Lowlands Nursery         NaN   
759                                MARY A WHALEN        NaN   
760                    Narrows Botanical Gardens        NaN   
761                   Pier 44 Waterfront Garden         NaN   
762  RETI Field Station at Gowanus Bay Terminal         NaN   

                                          site_address  \
0    Dwight Ave, Seagirt Blvd between Beach 38th St...   
1    Hylan Blvd & Satterlee St, Staten Island, Hyla...   
2    End of Sharrotts Ave at Hylan Blvd, Hylan Blvd...   
3                                                 None   
4                             W 79th St End, Manhattan   
..                                                 ...   
758                      25 9th St, Brooklyn, NY 11215   
759                        Pier 11, Brooklyn, NY 11231   
760              464 Bay Ridge Ave, Brooklyn, NY 11220   
761                                     298 Conover St   
762  South Red Hook, 699 Columbia St, Brooklyn, NY ...   

                                      site_description  \
0    This waterfront park is named, in part, for Ju...   
1    The site of a legendary display of American de...   
2                                                 None   
3                             Yellow trail nature path   
4    This site is considered a cultural resource. R...   
..                                                 ...   
758  The Lowlands Nursery offers plants that are we...   
759  Mary A. Whalen, known as the S.T. Kiddoo from ...   
760  Peaceful volunteer-run 4.5-acre garden featuri...   
761  With several flower blooms as well as a shaded...   
762  The RETI field station is a living, floating l...   

                                       hours_info  \
0       Sunrise to Sunset (April 1 to December 1)   
1       Sunrise to Sunset (April 1 to December 1)   
2                                            None   
3                                            None   
4       Sunrise to Sunset (April 1 to December 1)   
..                                            ...   
758  every Thursday & Saturday from 10 AM to 2 PM   
759              Monday thru Friday 10 am - 6 pm    
760                                  10 am - 5 pm   
761                                  Dawn to dusk   
762                                           NaN   

                                      open_close_date   fee  ...  \
0                                                None  None  ...   
1                                                None     Y  ...   
2                                                None  None  ...   
3                                                None  None  ...   
4                                              

## Create spatial dataframe

 - make map; red points are new or updated

In [51]:
hap_site_points = gpd.GeoDataFrame(new_hap_site_points, geometry=gpd.points_from_xy(new_hap_site_points['x'], new_hap_site_points['y']), crs="EPSG:4326")

In [52]:
m = folium.Map(
    location=[
        hap_site_points['y'].mean(), 
        hap_site_points['x'].mean()
    ], 
    zoom_start=10,
)

#creating a Marker for each point in df_sample. Each point will get a popup with their zip
for row in hap_site_points.itertuples():
        popup_text = f"Site Name: {row.site_name}<br>Activity Codes: {row.act_codes}"
        color = 'blue' if pd.isna(row.Creator) else 'red'
    
        folium.CircleMarker(
            location=[row.y,  row.x],
            radius=4,
            popup=popup_text,
            color=color,  # Change the color of the circle outline
            fill=True,
            fill_color='blue'
        ).add_to(m)
    
m   

### write out the geojson

In [53]:
hap_site_points.to_file('data/hap_site_points_20230804.geojson', driver='GeoJSON')